# Training the Algorithmic Traders

This notebook contains the code for generating and training the LSTM traders. We will be using the keras structures that are available with tensorflow as the basis for the struture.

In [225]:
import numpy as np #Import relevant packages
import pandas as pd
import math
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error
import glob
import csv

In [204]:
def unpack_data(filepath): #Returns a dictionary where each item is a df containing one run. One dict per generation.
    all_files = glob.glob(filepath + "/*.csv")
#    print(all_files)
    name_list = []
    datadict = {}
    for f in all_files:
        name_list.append(f[77:-4])
#        print(name_list)
    for i,n in enumerate(name_list):
        datadict[n] = pd.read_csv(all_files[i], header=0)
    for k, v in datadict.items():
        v.drop(columns=["Unnamed: 0", "volume", "spread", "10_MA", "50_MA"], inplace=True)
#        v.reset_index(drop=True)
#        v.index.name = "period"
    return datadict

In [207]:
gen0 = unpack_data("/Users/karangarg/Documents/Year 3 Modules/EC331/Code/rae_repo/gen0_sims/data") #Load gen0 data

In [193]:
#totaldf = pd.DataFrame(columns=["trading_price", "volume", "spread", "true_price", "10_MA", "50_MA"])
#dflist = []
    
#for k, v in gen0.items(): #Create a dataframe that contains all gen 0 data
#    dflist.append(v)
    
#totaldf = pd.concat(dflist)
#totaldf = totaldf.drop(columns=["volume", "spread", "10_MA", "50_MA"])

In [234]:
def format_data(datadict, window):
    x_data = []
    y_data = []
    for k, v in datadict.items():
        templist = []
        for index, row in v.iterrows():
            if index >= window:
#                print(f"we got one!{index}")
                y_data.append(v.iloc[index]["trading_price"])
                templist.extend(v.iloc[index-window:index]["trading_price"])
                templist.extend(v.iloc[index-window:index]["true_price"])
                x_data.append(tuple(templist))
                print(templist)
                templist.clear()
    return x_data, y_data

In [235]:
X, y = format_data(gen0, 10)

[100.0, 99.53, 99.22, 98.66, 98.38, 97.54, 96.98, 96.58, 96.3, 95.61, 100.0, 100.1, 100.2, 100.3, 100.65, 100.75, 101.79, 101.71, 101.52, 101.62]
[99.53, 99.22, 98.66, 98.38, 97.54, 96.98, 96.58, 96.3, 95.61, 94.96, 100.1, 100.2, 100.3, 100.65, 100.75, 101.79, 101.71, 101.52, 101.62, 101.72]
[99.22, 98.66, 98.38, 97.54, 96.98, 96.58, 96.3, 95.61, 94.96, 94.56, 100.2, 100.3, 100.65, 100.75, 101.79, 101.71, 101.52, 101.62, 101.72, 102.21]
[98.66, 98.38, 97.54, 96.98, 96.58, 96.3, 95.61, 94.96, 94.56, 93.6, 100.3, 100.65, 100.75, 101.79, 101.71, 101.52, 101.62, 101.72, 102.21, 102.31]
[98.38, 97.54, 96.98, 96.58, 96.3, 95.61, 94.96, 94.56, 93.6, 93.17, 100.65, 100.75, 101.79, 101.71, 101.52, 101.62, 101.72, 102.21, 102.31, 102.38]
[97.54, 96.98, 96.58, 96.3, 95.61, 94.96, 94.56, 93.6, 93.17, 92.8, 100.75, 101.79, 101.71, 101.52, 101.62, 101.72, 102.21, 102.31, 102.38, 102.84]
[96.98, 96.58, 96.3, 95.61, 94.96, 94.56, 93.6, 93.17, 92.8, 93.21, 101.79, 101.71, 101.52, 101.62, 101.72, 102.21

[83.0, 83.49, 83.78, 83.43, 82.58, 83.37, 82.41, 82.66, 83.45, 83.11, 116.64, 116.75, 116.86, 116.61, 116.72, 116.83, 116.94, 117.05, 119.7, 119.82]
[83.49, 83.78, 83.43, 82.58, 83.37, 82.41, 82.66, 83.45, 83.11, 82.26, 116.75, 116.86, 116.61, 116.72, 116.83, 116.94, 117.05, 119.7, 119.82, 120.3]
[83.78, 83.43, 82.58, 83.37, 82.41, 82.66, 83.45, 83.11, 82.26, 81.41, 116.86, 116.61, 116.72, 116.83, 116.94, 117.05, 119.7, 119.82, 120.3, 120.42]
[83.43, 82.58, 83.37, 82.41, 82.66, 83.45, 83.11, 82.26, 81.41, 80.56, 116.61, 116.72, 116.83, 116.94, 117.05, 119.7, 119.82, 120.3, 120.42, 120.54]
[82.58, 83.37, 82.41, 82.66, 83.45, 83.11, 82.26, 81.41, 80.56, 79.6, 116.72, 116.83, 116.94, 117.05, 119.7, 119.82, 120.3, 120.42, 120.54, 120.66]
[83.37, 82.41, 82.66, 83.45, 83.11, 82.26, 81.41, 80.56, 79.6, 79.955, 116.83, 116.94, 117.05, 119.7, 119.82, 120.3, 120.42, 120.54, 120.66, 120.78]
[82.41, 82.66, 83.45, 83.11, 82.26, 81.41, 80.56, 79.6, 79.955, 80.53, 116.94, 117.05, 119.7, 119.82, 120.3

[53.27, 52.31, 53.16, 54.15, 53.3, 52.34, 53.13, 53.98, 54.94, 55.73, 128.76, 128.89, 129.02, 129.15, 128.96, 129.09, 129.22, 129.35, 129.48, 129.61]
[52.31, 53.16, 54.15, 53.3, 52.34, 53.13, 53.98, 54.94, 55.73, 56.115, 128.89, 129.02, 129.15, 128.96, 129.09, 129.22, 129.35, 129.48, 129.61, 129.74]
[53.16, 54.15, 53.3, 52.34, 53.13, 53.98, 54.94, 55.73, 56.115, 56.0, 129.02, 129.15, 128.96, 129.09, 129.22, 129.35, 129.48, 129.61, 129.74, 129.87]
[54.15, 53.3, 52.34, 53.13, 53.98, 54.94, 55.73, 56.115, 56.0, 55.76, 129.15, 128.96, 129.09, 129.22, 129.35, 129.48, 129.61, 129.74, 129.87, 130.0]
[53.3, 52.34, 53.13, 53.98, 54.94, 55.73, 56.115, 56.0, 55.76, 55.42, 128.96, 129.09, 129.22, 129.35, 129.48, 129.61, 129.74, 129.87, 130.0, 129.91]
[52.34, 53.13, 53.98, 54.94, 55.73, 56.115, 56.0, 55.76, 55.42, 55.02, 129.09, 129.22, 129.35, 129.48, 129.61, 129.74, 129.87, 130.0, 129.91, 130.04]
[53.13, 53.98, 54.94, 55.73, 56.115, 56.0, 55.76, 55.42, 55.02, 54.06, 129.22, 129.35, 129.48, 129.61

[117.29, 118.21, 117.79, 118.63, 117.79, 118.69, 117.79, 118.73, 118.14, 119.06, 117.38, 117.49, 117.6, 117.71, 117.78, 117.89, 118.01, 118.13, 118.25, 117.93]
[118.21, 117.79, 118.63, 117.79, 118.69, 117.79, 118.73, 118.14, 119.06, 118.16, 117.49, 117.6, 117.71, 117.78, 117.89, 118.01, 118.13, 118.25, 117.93, 118.05]
[117.79, 118.63, 117.79, 118.69, 117.79, 118.73, 118.14, 119.06, 118.16, 119.08, 117.6, 117.71, 117.78, 117.89, 118.01, 118.13, 118.25, 117.93, 118.05, 118.17]
[118.63, 117.79, 118.69, 117.79, 118.73, 118.14, 119.06, 118.16, 119.08, 118.49, 117.71, 117.78, 117.89, 118.01, 118.13, 118.25, 117.93, 118.05, 118.17, 116.14]
[117.79, 118.69, 117.79, 118.73, 118.14, 119.06, 118.16, 119.08, 118.49, 117.54, 117.78, 117.89, 118.01, 118.13, 118.25, 117.93, 118.05, 118.17, 116.14, 116.49]
[118.69, 117.79, 118.73, 118.14, 119.06, 118.16, 119.08, 118.49, 117.54, 116.99, 117.89, 118.01, 118.13, 118.25, 117.93, 118.05, 118.17, 116.14, 116.49, 117.07]
[117.79, 118.73, 118.14, 119.06, 118.

[116.65, 116.2, 117.04, 116.09, 117.04, 116.09, 117.05, 116.59, 117.43, 117.75, 116.01, 116.17, 116.32, 116.43, 116.54, 116.65, 116.76, 116.87, 117.2, 117.31]
[116.2, 117.04, 116.09, 117.04, 116.09, 117.05, 116.59, 117.43, 117.75, 117.805, 116.17, 116.32, 116.43, 116.54, 116.65, 116.76, 116.87, 117.2, 117.31, 117.5]
[117.04, 116.09, 117.04, 116.09, 117.05, 116.59, 117.43, 117.75, 117.805, 118.12, 116.32, 116.43, 116.54, 116.65, 116.76, 116.87, 117.2, 117.31, 117.5, 117.61]
[116.09, 117.04, 116.09, 117.05, 116.59, 117.43, 117.75, 117.805, 118.12, 117.36, 116.43, 116.54, 116.65, 116.76, 116.87, 117.2, 117.31, 117.5, 117.61, 118.03]
[117.04, 116.09, 117.05, 116.59, 117.43, 117.75, 117.805, 118.12, 117.36, 118.33, 116.54, 116.65, 116.76, 116.87, 117.2, 117.31, 117.5, 117.61, 118.03, 117.96]
[116.09, 117.05, 116.59, 117.43, 117.75, 117.805, 118.12, 117.36, 118.33, 118.64, 116.65, 116.76, 116.87, 117.2, 117.31, 117.5, 117.61, 118.03, 117.96, 117.98]
[117.05, 116.59, 117.43, 117.75, 117.805, 

...

[106.17, 105.19, 105.75, 106.26, 105.28, 105.85, 106.61, 105.67, 106.65, 105.75, 102.45, 102.55, 102.65, 102.75, 102.75, 102.85, 102.83, 102.93, 102.76, 102.86]
[105.19, 105.75, 106.26, 105.28, 105.85, 106.61, 105.67, 106.65, 105.75, 106.21, 102.55, 102.65, 102.75, 102.75, 102.85, 102.83, 102.93, 102.76, 102.86, 102.96]
[105.75, 106.26, 105.28, 105.85, 106.61, 105.67, 106.65, 105.75, 106.21, 107.13, 102.65, 102.75, 102.75, 102.85, 102.83, 102.93, 102.76, 102.86, 102.96, 103.06]
[106.26, 105.28, 105.85, 106.61, 105.67, 106.65, 105.75, 106.21, 107.13, 106.15, 102.75, 102.75, 102.85, 102.83, 102.93, 102.76, 102.86, 102.96, 103.06, 103.56]
[105.28, 105.85, 106.61, 105.67, 106.65, 105.75, 106.21, 107.13, 106.15, 106.69, 102.75, 102.85, 102.83, 102.93, 102.76, 102.86, 102.96, 103.06, 103.56, 103.66]
[105.85, 106.61, 105.67, 106.65, 105.75, 106.21, 107.13, 106.15, 106.69, 107.2, 102.85, 102.83, 102.93, 102.76, 102.86, 102.96, 103.06, 103.56, 103.66, 103.76]
[106.61, 105.67, 106.65, 105.75, 10

[142.49, 143.47, 142.53, 143.51, 142.53, 143.12, 144.06, 143.08, 144.02, 145.0, 135.09, 135.22, 135.35, 135.48, 135.61, 135.74, 135.87, 136.0, 135.96, 136.02]
[143.47, 142.53, 143.51, 142.53, 143.12, 144.06, 143.08, 144.02, 145.0, 144.01, 135.22, 135.35, 135.48, 135.61, 135.74, 135.87, 136.0, 135.96, 136.02, 136.15]
[142.53, 143.51, 142.53, 143.12, 144.06, 143.08, 144.02, 145.0, 144.01, 144.5, 135.35, 135.48, 135.61, 135.74, 135.87, 136.0, 135.96, 136.02, 136.15, 136.28]
[143.51, 142.53, 143.12, 144.06, 143.08, 144.02, 145.0, 144.01, 144.5, 145.22, 135.48, 135.61, 135.74, 135.87, 136.0, 135.96, 136.02, 136.15, 136.28, 136.41]
[142.53, 143.12, 144.06, 143.08, 144.02, 145.0, 144.01, 144.5, 145.22, 144.24, 135.61, 135.74, 135.87, 136.0, 135.96, 136.02, 136.15, 136.28, 136.41, 136.54]
[143.12, 144.06, 143.08, 144.02, 145.0, 144.01, 144.5, 145.22, 144.24, 144.75, 135.74, 135.87, 136.0, 135.96, 136.02, 136.15, 136.28, 136.41, 136.54, 136.67]
[144.06, 143.08, 144.02, 145.0, 144.01, 144.5, 145

[113.0, 113.86, 113.16, 114.12, 113.75, 113.92, 114.78, 113.9, 114.38, 114.88, 116.34, 116.25, 116.36, 116.47, 116.58, 116.91, 116.89, 117.34, 117.45, 117.56]
[113.86, 113.16, 114.12, 113.75, 113.92, 114.78, 113.9, 114.38, 114.88, 114.18, 116.25, 116.36, 116.47, 116.58, 116.91, 116.89, 117.34, 117.45, 117.56, 117.89]
[113.16, 114.12, 113.75, 113.92, 114.78, 113.9, 114.38, 114.88, 114.18, 115.0, 116.36, 116.47, 116.58, 116.91, 116.89, 117.34, 117.45, 117.56, 117.89, 118.27]
[114.12, 113.75, 113.92, 114.78, 113.9, 114.38, 114.88, 114.18, 115.0, 114.45, 116.47, 116.58, 116.91, 116.89, 117.34, 117.45, 117.56, 117.89, 118.27, 118.39]
[113.75, 113.92, 114.78, 113.9, 114.38, 114.88, 114.18, 115.0, 114.45, 115.31, 116.58, 116.91, 116.89, 117.34, 117.45, 117.56, 117.89, 118.27, 118.39, 118.51]
[113.92, 114.78, 113.9, 114.38, 114.88, 114.18, 115.0, 114.45, 115.31, 114.64, 116.91, 116.89, 117.34, 117.45, 117.56, 117.89, 118.27, 118.39, 118.51, 118.63]
[114.78, 113.9, 114.38, 114.88, 114.18, 115.0

[119.77, 120.77, 119.82, 120.77, 119.82, 120.58, 120.94, 120.02, 120.99, 120.07, 119.79, 119.46, 119.58, 119.7, 119.82, 119.94, 120.06, 120.18, 120.3, 120.42]
[120.77, 119.82, 120.77, 119.82, 120.58, 120.94, 120.02, 120.99, 120.07, 121.02, 119.46, 119.58, 119.7, 119.82, 119.94, 120.06, 120.18, 120.3, 120.42, 120.54]
[119.82, 120.77, 119.82, 120.58, 120.94, 120.02, 120.99, 120.07, 121.02, 120.22, 119.58, 119.7, 119.82, 119.94, 120.06, 120.18, 120.3, 120.42, 120.54, 120.66]
[120.77, 119.82, 120.58, 120.94, 120.02, 120.99, 120.07, 121.02, 120.22, 121.17, 119.7, 119.82, 119.94, 120.06, 120.18, 120.3, 120.42, 120.54, 120.66, 120.78]
[119.82, 120.58, 120.94, 120.02, 120.99, 120.07, 121.02, 120.22, 121.17, 120.38, 119.82, 119.94, 120.06, 120.18, 120.3, 120.42, 120.54, 120.66, 120.78, 120.9]
[120.58, 120.94, 120.02, 120.99, 120.07, 121.02, 120.22, 121.17, 120.38, 121.33, 119.94, 120.06, 120.18, 120.3, 120.42, 120.54, 120.66, 120.78, 120.9, 121.52]
[120.94, 120.02, 120.99, 120.07, 121.02, 120.2

[148.49, 149.44, 149.13, 149.89, 148.94, 149.91, 148.96, 149.93, 150.43, 149.48, 148.61, 148.76, 148.91, 149.06, 149.21, 149.36, 149.51, 149.84, 149.99, 150.14]
[149.44, 149.13, 149.89, 148.94, 149.91, 148.96, 149.93, 150.43, 149.48, 150.48, 148.76, 148.91, 149.06, 149.21, 149.36, 149.51, 149.84, 149.99, 150.14, 150.17]
[149.13, 149.89, 148.94, 149.91, 148.96, 149.93, 150.43, 149.48, 150.48, 150.68, 148.91, 149.06, 149.21, 149.36, 149.51, 149.84, 149.99, 150.14, 150.17, 150.32]
[149.89, 148.94, 149.91, 148.96, 149.93, 150.43, 149.48, 150.48, 150.68, 149.88, 149.06, 149.21, 149.36, 149.51, 149.84, 149.99, 150.14, 150.17, 150.32, 150.47]
[148.94, 149.91, 148.96, 149.93, 150.43, 149.48, 150.48, 150.68, 149.88, 150.85, 149.21, 149.36, 149.51, 149.84, 149.99, 150.14, 150.17, 150.32, 150.47, 150.62]
[149.91, 148.96, 149.93, 150.43, 149.48, 150.48, 150.68, 149.88, 150.85, 150.12, 149.36, 149.51, 149.84, 149.99, 150.14, 150.17, 150.32, 150.47, 150.62, 150.77]
[148.96, 149.93, 150.43, 149.48, 1

[(100.0, 99.53, 99.22, 98.66, 98.38, 97.54, 96.98, 96.58, 96.3, 95.61, 100.0, 100.1, 100.2, 100.3, 100.65, 100.75, 101.79, 101.71, 101.52, 101.62), (99.53, 99.22, 98.66, 98.38, 97.54, 96.98, 96.58, 96.3, 95.61, 94.96, 100.1, 100.2, 100.3, 100.65, 100.75, 101.79, 101.71, 101.52, 101.62, 101.72), (99.22, 98.66, 98.38, 97.54, 96.98, 96.58, 96.3, 95.61, 94.96, 94.56, 100.2, 100.3, 100.65, 100.75, 101.79, 101.71, 101.52, 101.62, 101.72, 102.21), (98.66, 98.38, 97.54, 96.98, 96.58, 96.3, 95.61, 94.96, 94.56, 93.6, 100.3, 100.65, 100.75, 101.79, 101.71, 101.52, 101.62, 101.72, 102.21, 102.31), (98.38, 97.54, 96.98, 96.58, 96.3, 95.61, 94.96, 94.56, 93.6, 93.17, 100.65, 100.75, 101.79, 101.71, 101.52, 101.62, 101.72, 102.21, 102.31, 102.38), (97.54, 96.98, 96.58, 96.3, 95.61, 94.96, 94.56, 93.6, 93.17, 92.8, 100.75, 101.79, 101.71, 101.52, 101.62, 101.72, 102.21, 102.31, 102.38, 102.84), (96.98, 96.58, 96.3, 95.61, 94.96, 94.56, 93.6, 93.17, 92.8, 93.21, 101.79, 101.71, 101.52, 101.62, 101.72,

In [ ]:
model=Sequential() #Set up the architecture of the model
model.add(LSTM(units=50, input_shape = (X_train.shape[1], 1)))
model.add(Dropout(0.2))


model.add(LSTM(units = 50, return_sequences = True))
model.add(Dropout(0.2))

model.add(LSTM(units = 50, return_sequences = True))
model.add(Dropout(0.2))

model.add(LSTM(units = 50))
model.add(Dropout(0.2))

model.add(Dense(units = 1))

In [ ]:
model.compile(optimizer = 'nadam', loss = 'mean_squared_error') #Compile the network

model.fit(X_train, y_train, epochs = 100, batch_size = 32) #Train the model

In [227]:
lista = []
lista.extend(gen0sim3.iloc[0:3]["trading_price"])
lista.extend(gen0sim3.iloc[0:3]["true_price"])
print(lista)
listb = [1, 2, 3]
lista.append(listb)
print(lista)

[100.0, 100.77, 100.99, 100.0, 100.1, 100.19]
[100.0, 100.77, 100.99, 100.0, 100.1, 100.19, [1, 2, 3]]
